###### Imports and Settings

In [1]:
import folium
import geopandas as gpd
import pandas as pd
import branca
import branca.colormap as cm
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 150)

# Map Clusters  

Here the shapefile of the places coming from the data prep for all places in the US along with their clusters as established by the K-Means clustering algorithm. Using Folium, interactive maps are created to visualize where these peer communities are located.

In [2]:
geo = gpd.read_file('../data/geo/ALLPLACESCLUSTER.shp')

In [4]:
geo.head(2)

GEOID        NAME         NAMELSAD  SQMILES StateFIPS PlaceFIPS   09pop   14pop   19pop  hhsize  drive   ST%    ST   LT%     LT    State  \
0  0115136     Clanton     Clanton city    22.84        01     15136  8689.0  8672.0  8700.0    2.44   31.1  0.32  28.0  0.13   11.0  Alabama   
1  0163336  Rainsville  Rainsville city    20.62        01     63336  4898.0  4984.0  5041.0    2.66   21.5  1.14  57.0  2.92  143.0  Alabama   

   19density  14density  09density  STDensity  ST%Density  LTDensity  LT%Density       Place   CBSA  14permits  19permits  permreal   perm%  \
0     380.91     379.68     380.43       1.23        0.32       0.48        0.13     Clanton  13820       23.4       26.4       3.0   12.82   
1     244.47     241.71     237.54       2.76        1.14       6.93        2.92  Rainsville  99999       11.2       23.2      12.0  107.14   

   cluster                                           geometry  
0        0  POLYGON ((-86.68405 32.83101, -86.68383 32.831...  
1        1  POLYGON ((-85.89968 34.51085, -85.89943 34.511...

In [6]:
geo.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 90 entries, 0 to 89
Data columns (total 31 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   GEOID       90 non-null     object  
 1   NAME        90 non-null     object  
 2   NAMELSAD    90 non-null     object  
 3   SQMILES     90 non-null     float64 
 4   StateFIPS   90 non-null     object  
 5   PlaceFIPS   90 non-null     object  
 6   09pop       90 non-null     float64 
 7   14pop       90 non-null     float64 
 8   19pop       90 non-null     float64 
 9   hhsize      90 non-null     float64 
 10  drive       90 non-null     float64 
 11  ST%         90 non-null     float64 
 12  ST          90 non-null     float64 
 13  LT%         90 non-null     float64 
 14  LT          90 non-null     float64 
 15  State       90 non-null     object  
 16  19density   90 non-null     float64 
 17  14density   90 non-null     float64 
 18  09density   90 non-null     float64 
 19  ST

Set initial color return function for all clusters represented by distinct diverging colorscale.

In [7]:
def getcolor(feature):
    if feature['properties']['cluster'] == 0:
        return '#d53e4f'
    if feature['properties']['cluster'] == 1:
        return '#f46d43'
    if feature ['properties']['cluster'] == 2:
        return '#fdae61'
    if feature ['properties']['cluster'] == 3:
        return '#fee08b'
    if feature ['properties']['cluster'] ==4:
        return '#e6f598'
    if feature ['properties']['cluster'] == 5:
        return '#abdda4'
    if feature ['properties']['cluster'] == 6:
        return '#66c2a5'
    if feature ['properties']['cluster'] == 7:
        return '#3288bd'
    else:
        return 'black'

Use branca StepColormap to create a legend.

In [8]:
step = cm.StepColormap(
    ['#d53e4f', '#f46d43', '#fdae61', '#fee08b', '#e6f598', '#abdda4', '#66c2a5', '#3288bd'],
    vmin=0, vmax=8-1,
    caption='Cluster of Place')
step

Use a folium GeoJson object to create a visual, essentially a choropleth, of the clusters represented by these respective colors. Use the getcolor() function and style parameters to set what the polygons will look like, name the layer, and create a tooltip.

In [10]:
chor = folium.GeoJson(geo, smooth_factor = 1, style_function = lambda feature: {
    'fillColor' : getcolor(feature), 'weight' : 0, 'fillOpacity' : 1, 'line_opacity' : 1, 'line_color' : 'black', 'line_weight' : 1}, 
                     show = True,#ZCTA
                     name = 'Place Cluster', 
                     tooltip = folium.features.GeoJsonTooltip(
                                 fields=['cluster','NAMELSAD','19pop','19density','LT%'],
                                 aliases=['<b>Cluster:</b>', 'Place:', 'Population:', 'Population Density:', 'Long Term Growth:'],
                                 style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))

In [11]:
# clusters = folium.Map(location = [39.826135, -98.581124], 
#                       tiles = 'https://{s}.tile.jawg.io/jawg-light/{z}/{x}/{y}{r}.png?access-token={W3CY2Fn6YgQqHa7RR7esKG3Xilp4GApzYaKQnWd9JyyGoD431QfbYa48SCKgLWQI}', 
#                       attr = 'Jawg.Light',
#                       zoom_start = 15, control_scale = True)
# clusters.add_child(chor)
# clusters.add_child(step)
# clusters

In [12]:
clusters = folium.Map(location = [39.826135, -98.581124], 
                      tiles = 'cartodbpositron', zoom_start = 5, control_scale = True)
clusters.add_child(chor)
clusters.add_child(step)
clusters

## Now the Coopertown cluster will be visualized so that all other clusters are one color.

Set new color function only distinguishing Coopertown cluster (1).

In [13]:
def getcolor(feature):
    if feature['properties']['cluster'] == 1:
        return '#d53e4f'
    else:
        return '#abdda4'

Two colors, don't need a legend.

Use a folium GeoJson object to create a visual, essentially a choropleth, of the clusters represented by these respective colors. Use the getcolor() function and style parameters to set what the polygons will look like, name the layer, and create a tooltip.

In [11]:
chor = folium.GeoJson(geo, smooth_factor = 1, style_function = lambda feature: {
    'fillColor' : getcolor(feature), 'weight' : 0, 'fillOpacity' : 1, 'line_opacity' : 1, 'line_color' : 'black', 'line_weight' : 1},
                     show = True,
                     name = 'Place Cluster', 
                     tooltip = folium.features.GeoJsonTooltip(
                                 fields=['cluster','NAMELSAD','19pop','19density','LT%'],
                                 aliases=['<b>Cluster:</b>', 'Place:', 'Population:', 'Population Density:', 'Long Term Growth:'],
                                 style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))

In [8]:
clusters = folium.Map(location = [39.826135, -98.581124], 
                      #tiles = 'https://tiles.stadiamaps.com/tiles/alidade_smooth/{z}/{x}/{y}{r}.png', 
                      #attr = 'Stadia.AlidadeSmooth', 
                      zoom_start = 5, control_scale = True)
clusters.add_child(chor)
clusters.add_child(step)
clusters